*Import librairies*

In [1]:
import yfinance as yf
import pandas as pd
import numpy as np
import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.io as pio
import plotly.offline as pyo
from scipy.optimize import minimize

pyo.init_notebook_mode()
pd.set_option("display.max_columns", 101)

*Import Custom Functions*

In [2]:
import zozif
import zozif.plotly_dark_custom

*VARIABLES*

In [3]:
WIDTH = 900 
HEIGHT = 600

app_color = {
    "graph_bg": "rgb(221, 236, 255)",
    "graph_line": "rgb(8, 70, 151)",
    "graph_font":"rgb(2, 29, 65)"
}

chart_colors = [
    '#664DFF',
    '#893BFF',
    '#3CC5E8',
    '#2C93E8',
    '#0BEBDD',
    '#0073FF',
    '#00BDFF',
    '#A5E82C',
    '#FFBD42',
    '#FFCA30'
]

pio.templates.default = "plotly_dark_custom"

# ESSAY 1

## Introduction

### Stocks

In [4]:
stocks = {
 'Materials': {'Name': 'Newmont Corporation', 'Ticker': 'NEM'},
 'Communication Services': {'Name': 'Alphabet Inc.', 'Ticker': 'GOOGL'},
 'Consumer Discretionary': {'Name': 'Amazon.com Inc.', 'Ticker': 'AMZN'},
 'Consumer Staples': {'Name': 'PepsiCo Inc.', 'Ticker': 'PEP'},
 'Energy': {'Name': 'National Oilwell Varco Inc.', 'Ticker': 'NOV'},
 'Financial Services': {'Name': 'Bank of America Corp', 'Ticker': 'BAC'},
 'Healthcare': {'Name': 'HCA Healthcare', 'Ticker': 'HCA'},
 'Industrials': {'Name': 'Boeing Company', 'Ticker': 'BA'},
 'Real Estate': {'Name': 'Host Hotels & Resorts', 'Ticker': 'HST'},
 'Information Technology': {'Name': 'Apple Inc.', 'Ticker': 'AAPL'},
 'Utilities': {'Name': 'American Electric Power', 'Ticker': 'AEP'}
}

### Downloading data

In [5]:
complete_data = yf.download(
        tickers = [stocks[stock]['Ticker'] for stock in stocks],
        group_by = 'ticker',
        start="2018-06-30"
    )

[*********************100%***********************]  11 of 11 completed


In [6]:
market = yf.download(
    tickers = "^GSPC",
    start="2018-06-30"
)

market.dropna(how='all', inplace=True)
market_prices = market['Adj Close']
market_returns = market_prices.pct_change().dropna(how='all')
market_logs = np.log(1 + market_prices.pct_change()).dropna(how="all")
market_prices = market_prices.iloc[1:]
market.dropna(inplace=True)

[*********************100%***********************]  1 of 1 completed


In [7]:
stocks_name = []
for ticks in complete_data.columns.levels[0]:
    for stock in stocks:
        if ticks == stocks[stock]['Ticker']:
            stocks_name.append(stocks[stock]['Name'])

In [8]:
complete_data.columns.set_levels(stocks_name, level=0, inplace=True)

In [9]:
complete_data['Apple Inc.']

Open        High         Low       Close   Adj Close  \
Date                                                                     
2018-06-29   46.572498   46.797501   45.727501   46.277500   44.964947   
2018-07-02   45.955002   46.825001   45.855000   46.794998   45.467773   
2018-07-03   46.947498   46.987499   45.884998   45.980000   44.675892   
2018-07-05   46.314999   46.602501   46.070000   46.349998   45.035393   
2018-07-06   46.355000   47.107498   46.299999   46.992500   45.659668   
...                ...         ...         ...         ...         ...   
2020-10-15  118.720001  121.199997  118.150002  120.709999  120.709999   
2020-10-16  121.279999  121.550003  118.809998  119.019997  119.019997   
2020-10-19  119.959999  120.419998  115.660004  115.980003  115.980003   
2020-10-20  116.199997  118.980003  115.629997  117.510002  117.510002   
2020-10-21  116.669998  118.709999  116.449997  116.870003  116.870003   

                 Volume  
Date                     
2018-06-29   90950800.0  
2018-07-02   70925200.0  
2018-07-03   55819200.0  
2018-07-05   66416800.0  
2018-07-06   69940800.0  
...                 ...  
2020-10-15  112559200.0  
2020-10-16  115393800.0  
2020-10-19  120639300.0  
2020-10-20  124423700.0  
2020-10-21   89424000.0  

[584 rows x 6 columns]

### Statistics about stocks

In [10]:
complete_data.dropna(how="all", inplace=True)

In [11]:
complete_data.describe(include='all')

Host Hotels & Resorts                                                  \
                       Open        High         Low       Close   Adj Close   
count            583.000000  583.000000  583.000000  583.000000  583.000000   
mean              16.455866   16.652213   16.222316   16.435317   15.737942   
std                3.504483    3.456439    3.567141    3.504534    3.020538   
min                9.130000    9.700000    7.860000    9.060000    9.060000   
25%               12.455000   12.810000   11.985000   12.380000   12.310000   
50%               17.459999   17.590000   17.270000   17.459999   16.684502   
75%               19.010000   19.200001   18.799999   19.000000   17.919456   
max               21.940001   22.059999   21.570000   21.940001   20.303028   

                    HCA Healthcare                                      \
             Volume           Open        High         Low       Close   
count  5.830000e+02     583.000000  583.000000  583.000000  583.000000   
mean   8.490942e+06     126.805592  128.529863  125.017530  126.768628   
std    4.570837e+06      14.629685   14.113129   15.074638   14.654702   
min    1.251900e+06      67.000000   74.209999   58.380001   68.129997   
25%    5.519450e+06     120.850002  122.505001  119.120003  120.810001   
50%    7.508100e+06     130.000000  131.589996  128.320007  129.750000   
75%    9.977000e+06     136.355003  138.294998  134.600006  136.215004   
max    3.428470e+07     151.639999  151.970001  149.500000  151.039993   

                                Bank of America Corp                          \
        Adj Close        Volume                 Open        High         Low   
count  583.000000  5.830000e+02           583.000000  583.000000  583.000000   
mean   125.656233  1.943128e+06            28.150600   28.478662   27.830309   
std     14.366442  1.040801e+06             3.498234    3.399188    3.588696   
min     68.129997  4.550000e+05            19.260000   19.670000   17.950001   
25%    120.020607  1.215600e+06            25.495000   25.810000   25.100000   
50%    128.281433  1.646100e+06            28.379999   28.700001   28.049999   
75%    135.246796  2.349500e+06            30.224999   30.615001   30.090000   
max    150.530045  7.008100e+06            35.700001   35.720001   35.290001   

                                            Boeing Company              \
            Close   Adj Close        Volume           Open        High   
count  583.000000  583.000000  5.830000e+02     583.000000  583.000000   
mean    28.153654   27.339952  6.245370e+07     302.699743  306.702282   
std      3.498417    3.286542  2.635458e+07      89.724411   89.529450   
min     18.080000   17.830576  1.380540e+07      98.750000  103.570000   
25%     25.500000   25.195132  4.523455e+07     187.584999  192.704994   
50%     28.400000   27.337885  5.513240e+07     344.320007  347.579987   
75%     30.275001   29.145388  7.243635e+07     364.339996  368.465012   
max     35.639999   34.925472  1.818985e+08     446.010010  446.010010   

                                                         \
              Low       Close   Adj Close        Volume   
count  583.000000  583.000000  583.000000  5.830000e+02   
mean   298.181938  302.351234  297.074178  1.366772e+07   
std     90.313432   90.290715   86.960220  1.724084e+07   
min     89.000000   95.010002   95.010002  1.390900e+06   
25%    181.750000  188.800003  188.800003  3.285250e+06   
50%    339.489990  344.549988  336.093201  5.110400e+06   
75%    359.880005  363.889999  355.196350  1.802285e+07   
max    440.190002  440.619995  430.299988  1.032128e+08   

      American Electric Power                                                  \
                         Open        High         Low       Close   Adj Close   
count              583.000000  583.000000  583.000000  583.000000  583.000000   
mean                83.820000   84.626913   82.970343   83.869040   81.139031   
std              

In [12]:
prices = pd.concat([complete_data[name]['Adj Close'] for name in stocks_name], axis=1, keys=stocks_name)

In [13]:
returns = prices.pct_change().dropna(how="all")

In [14]:
logs = np.log(1 + prices.pct_change()).dropna(how="all")

In [15]:
prices = prices.iloc[1:, :]

#### Normal returns

In [16]:
stocks_stats = zozif.get_statistics(stocks_data=returns, market_data=market_returns, stocks_name=stocks_name)

In [17]:
market_stats = zozif.get_statistics(stocks_data=market_returns, market_data=market_returns, stocks_name=['S&P500'])

In [18]:
market_stats

Std  Annual Std    Mean  Geometric Mean  Median      Min     Max  \
S&P500  1.5786     25.0602  0.0528         10.6701  0.1075 -11.9841  9.3828   

         Kurtosis  Skewness  Alpha  Beta  VaR 95% HS  VaR 95% DN  \
S&P500  14.257317 -0.603421    0.0   1.0      -2.411     -2.5439   

        Systemic Risk  
S&P500         0.0249

In [19]:
stocks_stats

Std  Annual Std    Mean  Geometric Mean  \
Host Hotels & Resorts        2.6671     42.3397 -0.0623        -21.8295   
HCA Healthcare               2.8107     44.6182  0.0913         13.9930   
Bank of America Corp         2.5929     41.1609  0.0154         -4.4731   
Boeing Company               3.7890     60.1484 -0.0445        -25.4527   
American Electric Power      1.7339     27.5252  0.0735         15.8577   
Newmont Corporation          2.2471     35.6714  0.1201         27.0407   
National Oilwell Varco Inc.  3.8357     60.8899 -0.1921        -49.0215   
Apple Inc.                   2.3457     37.2366  0.1918         51.2226   
PepsiCo Inc.                 1.7003     26.9915  0.0687         14.6447   
Alphabet Inc.                1.9932     31.6408  0.0783         15.8458   
Amazon.com Inc.              2.1586     34.2665  0.1312         31.2435   

                             Median      Min      Max   Kurtosis  Skewness  \
Host Hotels & Resorts        0.0903 -15.6880  17.0974   8.553049  0.397792   
HCA Healthcare               0.0903 -19.0161  22.5598  13.582244  0.434519   
Bank of America Corp         0.0903 -15.3974  17.7962  10.861363  0.237134   
Boeing Company               0.0903 -23.8484  24.3186  12.174367  0.267715   
American Electric Power      0.0903 -11.5827  11.6826  13.429628 -0.008276   
Newmont Corporation          0.0903 -11.1161  14.0182   8.118633  0.403179   
National Oilwell Varco Inc.  0.0903 -28.9541  21.4876   9.399950 -0.313578   
Apple Inc.                   0.0903 -12.8647  11.9808   5.568029 -0.165548   
PepsiCo Inc.                 0.0903 -11.4283  12.9366  18.860947 -0.045731   
Alphabet Inc.                0.0903 -11.6342   9.6202   5.614543 -0.134361   
Amazon.com Inc.              0.0903  -7.9221   9.4452   2.408757  0.109673   

                                Alpha      Beta  VaR 95% HS  VaR 95% DN  \
Host Hotels & Resorts        0.000764  0.379762     -3.8954     -4.4493   
HCA Healthcare               0.000203  0.355724     -3.6549     -4.5319   
Bank of America Corp         0.000451  0.498584     -3.9800     -4.2495   
Boeing Company               0.000650  0.275072     -4.8497     -6.2769   
American Electric Power      0.000158  0.502744     -2.2676     -2.7786   
Newmont Corporation          0.000350  0.148254     -3.3327     -3.5760   
National Oilwell Varco Inc.  0.001024  0.258314     -5.6739     -6.5013   
Apple Inc.                  -0.000517  0.544508     -3.2635     -3.6665   
PepsiCo Inc.                 0.000053  0.691586     -2.1229     -2.7280   
Alphabet Inc.                0.000027  0.640123     -3.0090     -3.2002   
Amazon.com Inc.             -0.000094  0.473999     -3.3236     -3.4194   

                             Systemic Risk  
Host Hotels & Resorts               0.0036  
HCA Healthcare                      0.0032  
Bank of America Corp                0.0062  
Boeing Company                      0.0019  
American Electric Power             0.0063  
Newmont Corporation                 0.0005  
National Oilwell Varco Inc.         0.0017  
Apple Inc.                          0.0074  
PepsiCo Inc.                        0.0119  
Alphabet Inc.                       0.0102  
Amazon.com Inc.                     0.0056

#### Log Returns

In [20]:
market_stats_logs = zozif.get_statistics(stocks_data=market_logs, market_data=market_logs, stocks_name=['S&P500'])

In [21]:
stocks_stats_logs = zozif.get_statistics(stocks_data=logs, market_data=market_logs, stocks_name=stocks_name)

In [22]:
market_stats_logs

Std  Annual Std    Mean  Geometric Mean  Median      Min     Max  \
S&P500  1.5884     25.2152  0.0402          7.1701  0.1075 -12.7652  8.9683   

         Kurtosis  Skewness  Alpha  Beta  VaR 95% HS  VaR 95% DN  \
S&P500  15.348637 -0.985721    0.0   1.0     -2.4406     -2.5725   

        Systemic Risk  
S&P500         0.0252

In [23]:
stocks_stats_logs

Std  Annual Std    Mean  Geometric Mean  \
Host Hotels & Resorts        2.6642     42.2930 -0.0977        -28.5541   
HCA Healthcare               2.8070     44.5590  0.0520          3.1414   
Bank of America Corp         2.5951     41.1965 -0.0182        -12.3019   
Boeing Company               3.8089     60.4645 -0.1166        -38.2247   
American Electric Power      1.7366     27.5671  0.0584         11.5154   
Newmont Corporation          2.2396     35.5530  0.0950         19.2636   
National Oilwell Varco Inc.  3.9013     61.9313 -0.2674        -58.3256   
Apple Inc.                   2.3506     37.3149  0.1641         40.9637   
PepsiCo Inc.                 1.7047     27.0605  0.0542         10.4904   
Alphabet Inc.                1.9973     31.7063  0.0584         10.1417   
Amazon.com Inc.              2.1556     34.2183  0.1079         23.7781   

                             Median      Min      Max   Kurtosis  Skewness  \
Host Hotels & Resorts        0.0902 -17.0646  15.7836   8.260072 -0.010619   
HCA Healthcare               0.0902 -21.0920  20.3429  13.032612 -0.195707   
Bank of America Corp         0.0902 -16.7205  16.3786  10.616167 -0.250585   
Boeing Company               0.0902 -27.2444  21.7677  12.990571 -0.548232   
American Electric Power      0.0902 -12.3103  11.0491  13.240247 -0.401667   
Newmont Corporation          0.0902 -11.7839  13.1188   7.452691  0.081364   
National Oilwell Varco Inc.  0.0902 -34.1844  19.4642  13.023768 -1.049501   
Apple Inc.                   0.0902 -13.7708  11.3157   5.819943 -0.431266   
PepsiCo Inc.                 0.0902 -12.1358  12.1656  19.436631 -0.578361   
Alphabet Inc.                0.0902 -12.3685   9.1852   5.836726 -0.362133   
Amazon.com Inc.              0.0902  -8.2535   9.0254   2.387350 -0.031454   

                                Alpha      Beta  VaR 95% HS  VaR 95% DN  \
Host Hotels & Resorts        0.000782  0.388309     -3.9733     -4.4800   
HCA Healthcare               0.000212  0.366827     -3.7233     -4.5651   
Bank of America Corp         0.000494  0.502573     -4.0613     -4.2868   
Boeing Company               0.000730  0.281404     -4.9712     -6.3817   
American Electric Power      0.000108  0.503123     -2.2937     -2.7980   
Newmont Corporation          0.000264  0.145672     -3.3896     -3.5889   
National Oilwell Varco Inc.  0.001093  0.258368     -5.8413     -6.6844   
Apple Inc.                  -0.000497  0.547969     -3.3180     -3.7023   
PepsiCo Inc.                 0.000025  0.695510     -2.1457     -2.7497   
Alphabet Inc.                0.000026  0.644364     -3.0552     -3.2269   
Amazon.com Inc.             -0.000114  0.478809     -3.3800     -3.4377   

                             Systemic Risk  
Host Hotels & Resorts               0.0038  
HCA Healthcare                      0.0034  
Bank of America Corp                0.0064  
Boeing Company                      0.0020  
American Electric Power             0.0064  
Newmont Corporation                 0.0005  
National Oilwell Varco Inc.         0.0017  
Apple Inc.                          0.0076  
PepsiCo Inc.                        0.0122  
Alphabet Inc.                       0.0105  
Amazon.com Inc.                     0.0058

**Apple Analysis**

In [24]:
fig = px.line(x=prices['Apple Inc.'].index, y=prices['Apple Inc.'])
fig.update_xaxes(rangeslider_visible=True)

fig.update_layout(
    width=WIDTH, 
    height=HEIGHT,
    title='Apple Analysis during the COVID',
    yaxis_title='Closing Price',
    xaxis_title='Date',
    shapes = [dict(
        x0='2020-02-15', x1='2020-02-15', y0=0, y1=1, xref='x', yref='paper',
        line_width=2)],
    annotations=[dict(
        x='2020-02-17', y=0.95, xref='x', yref='paper',
        showarrow=False, xanchor='left', text='COVID Begins')],
    yaxis=dict(
    ticksuffix=' $'
    ),

)

pyo.iplot(fig)

**Amazon Analysis**

In [25]:
fig = go.Figure(data=[go.Candlestick(x=complete_data['Amazon.com Inc.'].index,
                open=complete_data['Amazon.com Inc.'].Open,
                high=complete_data['Amazon.com Inc.'].High,
                low=complete_data['Amazon.com Inc.'].Low,
                close=complete_data['Amazon.com Inc.'].Close)])

fig.update_layout(
    width=WIDTH, 
    height=HEIGHT,
    title='Amazon.com Analysis during the COVID',
    yaxis_title='Prices',
    shapes = [dict(
        x0='2020-02-15', x1='2020-02-15', y0=0, y1=1, xref='x', yref='paper',
        line_width=2)],
    annotations=[dict(
        x='2020-02-17', y=0.95, xref='x', yref='paper',
        showarrow=False, xanchor='left', text='COVID Begins')],
    yaxis=dict(
    ticksuffix=' $'
    ),
)

pyo.iplot(fig)

**Boeing Company Analysis**

In [26]:
colors = np.where(logs['Boeing Company'] < 0, 'red', 'green')

# Create figure with secondary y-axis
fig = make_subplots(specs=[[{"secondary_y": True}]])

# Add traces
fig.add_trace(
    go.Scatter(x=prices['Boeing Company'].index, 
               y=prices['Boeing Company'], 
               name="Closing Prices", 
               yaxis="y"),
    secondary_y=False
)

fig.add_trace(
    go.Bar(x=logs['Boeing Company'].index, 
           y=(logs['Boeing Company'] * 100), 
           name="Returns", 
           marker_color=colors, 
           yaxis="y1"),
    secondary_y=True
)

# Set x-axis title
fig.update_xaxes(title_text="Date")

fig.update_layout(
    width=WIDTH, 
    height=HEIGHT,
    title='Boeing Company Analysis during the COVID',
    yaxis=dict(
    title="TSLA Close's Prices",
    ticksuffix=' $'

    ),
    yaxis2=dict(
        title="TSLA Returns",
        ticksuffix = '%'
    ),
    shapes = [dict(
        x0='2020-02-15', x1='2020-02-15', 
        y0=0, y1=1, 
        xref='x', yref='paper',
        line_width=2)],
    annotations=[dict(
        x='2020-02-17', y=0.95, 
        xref='x', yref='paper',
        showarrow=False, xanchor='left', 
        text='COVID Begins')]
)

pyo.iplot(fig)

**Compare Stocks**

In [27]:
fig = go.Figure()

visible = [False] * len(prices.columns)
visible[0] = True

for i, name in enumerate(prices.columns):
    fig.add_trace(
        go.Scatter(
            x = prices[name].index,
            y = prices[name],
            name = name,
            visible=visible[i]
        )
    )

buttons = []

for i, name in enumerate(prices.columns):
    false_true = [False] * len(prices.columns)
    false_true[i] = True
    buttons.append(
        dict(label = name,
                method = 'update',
                args = [{'visible': false_true}])
    )

fig.update_layout(

    updatemenus=[
        dict(buttons=buttons,
        direction="down",
        pad={"r": 10, "t": 10},
        x=0.8,
        xanchor="left",
        y=1.2,
        yanchor="top",
        active=0,
        )],
)


fig.update_layout(
    width=WIDTH, 
    height=HEIGHT,
    title='Two years in S&P500',
    yaxis_title='Closing Prices',
    shapes = [dict(
        x0='2020-02-15', x1='2020-02-15', 
        y0=0, y1=1, 
        xref='x', yref='paper',
        line_width=2)],

    annotations=[
        dict(x='2020-02-17', y=0.95, 
        xref='x', yref='paper',
        showarrow=False, xanchor='left', 
        text='COVID Begins'),
        
        dict(text="Choose Stocks:", showarrow=False,
        x=0.61, xanchor='left', 
        y=1.17, yanchor="top",
        yref='paper', xref='paper',
        font=dict(size=18))
        ],

    yaxis=dict(
    ticksuffix=' $'
    ),
)


pyo.iplot(fig)

## Question 1

## Question 2

### Equal Weighted Portfolio

In [28]:
weights = [1/len(logs.columns)]*len(logs.columns)

equal_weighted_portfolio_norm_returns = (returns*weights).sum(axis=1)
equal_weighted_portfolio_logs_returns = (logs*weights).sum(axis=1)

In [29]:
eq_w_portfolio_stats = zozif.get_statistics(stocks_data=equal_weighted_portfolio_logs_returns, market_data=market_logs, stocks_name=['Eq W Portfolio'])

In [30]:
eq_w_portfolio_stats

Std  Annual Std    Mean  Geometric Mean  Median      Min  \
Eq W Portfolio  1.7691     28.0834  0.0082         -1.9197  0.0814 -12.9344   

                   Max   Kurtosis  Skewness     Alpha      Beta  VaR 95% HS  \
Eq W Portfolio  9.3989  13.917295 -1.224556  0.000333  0.846389     -2.3802   

                VaR 95% DN  Systemic Risk  
Eq W Portfolio     -2.9017         0.0181

## Question 3

### Efficient portfolio

In [31]:
stocks

{'Materials': {'Name': 'Newmont Corporation', 'Ticker': 'NEM'},
 'Communication Services': {'Name': 'Alphabet Inc.', 'Ticker': 'GOOGL'},
 'Consumer Discretionary': {'Name': 'Amazon.com Inc.', 'Ticker': 'AMZN'},
 'Consumer Staples': {'Name': 'PepsiCo Inc.', 'Ticker': 'PEP'},
 'Energy': {'Name': 'National Oilwell Varco Inc.', 'Ticker': 'NOV'},
 'Financial Services': {'Name': 'Bank of America Corp', 'Ticker': 'BAC'},
 'Healthcare': {'Name': 'HCA Healthcare', 'Ticker': 'HCA'},
 'Industrials': {'Name': 'Boeing Company', 'Ticker': 'BA'},
 'Real Estate': {'Name': 'Host Hotels & Resorts', 'Ticker': 'HST'},
 'Information Technology': {'Name': 'Apple Inc.', 'Ticker': 'AAPL'},
 'Utilities': {'Name': 'American Electric Power', 'Ticker': 'AEP'}}

In [32]:
base_selection = ['Amazon.com Inc.', 'HCA Healthcare', 'Apple Inc.', 'American Electric Power']

In [33]:
%%time
num_ports = 10000

simulation = zozif.monte_carlo(logs[base_selection], num_ports, geometric=True)

CPU times: user 13.7 s, sys: 0 ns, total: 13.7 s
Wall time: 13.7 s


In [34]:
allocation = zozif.get_allocation(simulation['weights'], simulation['returns'], 
                                  simulation['volatility'], simulation['sharpe'], 
                                  logs[base_selection])

allocation

Amazon.com Inc.  HCA Healthcare  Apple Inc.  \
Max Sharpe Allocation                 1.00            0.21       83.43   
Min Volatility Allocation            30.27           11.52        1.68   

                           American Electric Power  Returns  Volatility  \
Max Sharpe Allocation                        15.35    36.19       33.14   
Min Volatility Allocation                    56.53    14.76       23.17   

                           Sharpe Ratio  
Max Sharpe Allocation              1.09  
Min Volatility Allocation          0.64

In [35]:
efficient_frontier = go.Figure(go.Scatter(
    x=simulation['volatility'],
    y=simulation['returns'],
    marker=dict(
        size=5,
        color=simulation['sharpe'],
        colorbar=dict(
            title="Colorbar"
        ),
    ),
    mode="markers",
    name=f"Portfolios ({num_ports})"))

efficient_frontier.add_trace(go.Scatter(
    x=[allocation.iloc[0, 5]/100],
    y=[allocation.iloc[0, 4]/100],
    marker={'color':'red'},
    mode='markers',
    name='Efficient Portfolio'
))

efficient_frontier.add_trace(go.Scatter(
    x=[allocation.iloc[1, 5]/100],
    y=[allocation.iloc[1, 4]/100],
    marker={'color':'green'},
    mode='markers',
    marker_symbol='x',
    name='Min Volatility Portfolio'
))

efficient_frontier.update_layout(
    height=HEIGHT,
    width=WIDTH,
    legend=dict(
        yanchor="top",
        y=1.2,
        xanchor="left",
        x=1
        ),
    title='Simulated Portfolio Optimization based on Efficient Frontier'
)            


pyo.iplot(efficient_frontier)

In [36]:
# create constraint variable
cons = ({'type':'eq','fun':zozif.check_sum})

# create weight boundaries
bounds = tuple((0,1) for i in range(len(base_selection)))

# initial guess
init_guess = [1/len(base_selection)]*len(base_selection)

In [45]:
%%time

opt_results = minimize(zozif.neg_sharpe, init_guess, args=(returns[base_selection]),
                    method='SLSQP', bounds=bounds, constraints=cons)

CPU times: user 53.8 ms, sys: 3.9 ms, total: 57.7 ms
Wall time: 56.2 ms


In [46]:
print(base_selection)
print([i.round(2) for i in opt_results['x']*100])

['Amazon.com Inc.', 'HCA Healthcare', 'Apple Inc.', 'American Electric Power']
[0.0, 0.0, 90.32, 9.68]


In [47]:
pd.DataFrame(data=[i.round(2) for i in opt_results['x']*100],
            index=base_selection,
            columns=['Allocation']).T

Amazon.com Inc.  HCA Healthcare  Apple Inc.  \
Allocation              0.0             0.0       90.32   

            American Electric Power  
Allocation                     9.68

In [48]:
zozif.get_ret_vol_sr(returns[base_selection], opt_results.x)

array([0.47798343, 0.34657566, 1.37916038])

In [41]:
zozif.get_ret_vol_sr(logs[base_selection], [0, 0, 0.97, 0.3])

array([0.43189454, 0.39869043, 1.08328295])

# DRAFT

In [42]:
from pypfopt.efficient_frontier import EfficientFrontier
from pypfopt import risk_models
from pypfopt import expected_returns

In [43]:
mu = expected_returns.mean_historical_return(prices[base_selection])
S = risk_models.sample_cov(prices[base_selection])

In [44]:
ef = EfficientFrontier(mu, S)
weights = ef.max_sharpe() #Maximize the Sharpe ratio, and get the raw weights

cleaned_weights = ef.clean_weights() 

print(cleaned_weights) 
#Note the weights may have some rounding error, meaning they may not add up exactly to 1 but should be close
ef.portfolio_performance(verbose=True)

OrderedDict([('Amazon.com Inc.', 0.0), ('HCA Healthcare', 0.0), ('Apple Inc.', 0.97062), ('American Electric Power', 0.02938)])
Expected annual return: 49.6%
Annual volatility: 36.5%
Sharpe Ratio: 1.30


(0.4956528449882484, 0.3646086605510689, 1.3045571771919722)